In [1]:
import numpy as np
import cv2
from pathlib import Path
from PIL import Image
from skimage.color import rgb2gray
from skimage.feature import hog
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.svm import LinearSVC
from sklearn.pipeline import Pipeline
from sklearn.model_selection import StratifiedKFold, ParameterGrid, train_test_split
from sklearn.metrics import accuracy_score
from joblib import dump, load
from tqdm import tqdm
import matplotlib.pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages
import time
import os
import gc


In [2]:
# configs
DATA_DIR = Path("../data/OCT2017 /train")
TARGET_SIZE = 128
IMG_EXTS = (".jpg", ".jpeg", ".png", ".bmp", ".tif", ".tiff")
BATCH_SIZE = 64
RANDOM_STATE = 192

# Control subset size for grid search
SUBSET_SIZE = 0.2  # Use 20% of data for grid search (set to 1.0 to use all data)
MIN_SAMPLES_PER_CLASS = 50  # Minimum samples per class in subset

CHECKPOINT_PATH = Path("checkpoints/tuning_state.pkl")
BEST_MODEL_PATH = Path("checkpoints/best_model.pkl")
REPORTS_DIR = Path("reports")
REPORTS_DIR.mkdir(parents=True, exist_ok=True)
PDF_PATH = REPORTS_DIR / "feature_examples.pdf"



In [3]:
# dataloader etc
def load_and_preprocess_image(path, target_size=TARGET_SIZE):
    img = Image.open(path).convert("RGB")
    w, h = img.size
    scale = target_size / max(w, h)
    new_w, new_h = int(w * scale), int(h * scale)
    img = img.resize((new_w, new_h), Image.LANCZOS)
    canvas = Image.new("RGB", (target_size, target_size), (255, 255, 255))
    canvas.paste(img, ((target_size - new_w) // 2, (target_size - new_h) // 2))
    return np.asarray(canvas)


def enumerate_paths_and_labels(base_dir=DATA_DIR):
    classes = sorted([d.name for d in base_dir.iterdir() if d.is_dir()])
    label_map = {name: idx for idx, name in enumerate(classes)}
    paths, labels = [], []
    for name in classes:
        for p in sorted((base_dir / name).glob("*")):
            if p.suffix.lower() in IMG_EXTS:
                paths.append(p)
                labels.append(label_map[name])
    y = np.array(labels, dtype=np.int64)
    return paths, y, label_map


def create_stratified_subset(paths, y, subset_size=SUBSET_SIZE, min_per_class=MIN_SAMPLES_PER_CLASS,
                             random_state=RANDOM_STATE):
    if subset_size >= 1.0 and isinstance(subset_size, float):
        print(f"[INFO] Using full dataset (subset_size={subset_size})")
        return paths, y, np.arange(len(paths))

    n_total = len(paths)
    n_classes = len(np.unique(y))

    # Calculate target size
    if isinstance(subset_size, float) and 0 < subset_size < 1:
        target_size = int(n_total * subset_size)
    else:
        target_size = int(subset_size)

    # Ensure minimum samples per class
    min_total = min_per_class * n_classes
    if target_size < min_total:
        print(f"[WARNING] Requested subset size {target_size} < minimum {min_total}")
        print(f"[WARNING] Increasing to {min_total} samples ({min_per_class} per class)")
        target_size = min_total

    # Calculate stratified split ratio
    subset_ratio = min(target_size / n_total, 1.0)

    # Create stratified subset
    indices = np.arange(len(paths))
    subset_indices, _ = train_test_split(
        indices,
        train_size=subset_ratio,
        stratify=y,
        random_state=random_state
    )

    subset_paths = [paths[i] for i in subset_indices]
    subset_y = y[subset_indices]

    # Print statistics
    print(f"\n[SUBSET] Created stratified subset:")
    print(f"  Original size: {n_total}")
    print(f"  Subset size: {len(subset_paths)} ({len(subset_paths) / n_total * 100:.1f}%)")
    print(f"  Samples per class:")
    for label in np.unique(subset_y):
        count = np.sum(subset_y == label)
        orig_count = np.sum(y == label)
        print(f"    Class {label}: {count} / {orig_count} ({count / orig_count * 100:.1f}%)")

    return subset_paths, subset_y, subset_indices


def batch_iterator(paths, indices=None, batch_size=BATCH_SIZE):
    if indices is None:
        indices = np.arange(len(paths))
    n = len(indices)
    for i in range(0, n, batch_size):
        idxs = indices[i:i + batch_size]
        imgs = [load_and_preprocess_image(paths[j]) for j in idxs]
        yield np.stack(imgs), idxs


# HOG
class HOGTransformer(BaseEstimator, TransformerMixin):
    """
    Converts (N, H, W, 3) uint8 images -> (N, F) HOG feature vectors (float64).
    """

    def __init__(self, orientations=9, pixels_per_cell=(8, 8), cells_per_block=(2, 2), block_norm="L2-Hys",
                 visualize=False):
        self.orientations = orientations
        self.pixels_per_cell = pixels_per_cell
        self.cells_per_block = cells_per_block
        self.block_norm = block_norm
        self.visualize = visualize

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        feats = []
        for img in X:
            g = rgb2gray(img.astype(np.float32) / 255.0)
            f = hog(
                g,
                orientations=self.orientations,
                pixels_per_cell=self.pixels_per_cell,
                cells_per_block=self.cells_per_block,
                block_norm=self.block_norm,
                feature_vector=True
            )
            feats.append(f)
        return np.vstack(feats)

    def transform_with_viz(self, img_single):
        """Return (features, hog_image) for one image, to visualize in the PDF."""
        g = rgb2gray(img_single.astype(np.float32) / 255.0)
        f, hog_img = hog(
            g,
            orientations=self.orientations,
            pixels_per_cell=self.pixels_per_cell,
            cells_per_block=self.cells_per_block,
            block_norm=self.block_norm,
            visualize=True,
            feature_vector=True
        )
        return f, hog_img


# SIFT
class SIFTTransformer(BaseEstimator, TransformerMixin):
    """
    Extracts SIFT descriptors per image and pools to a fixed-length vector:
        feature = concat(mean(desc, axis=0), std(desc, axis=0), [count])
    Resulting dimension = 128 + 128 + 1 = 257
    """

    def __init__(self, n_features=0, contrastThreshold=0.04, edgeThreshold=10, sigma=1.6):
        self.n_features = n_features
        self.contrastThreshold = contrastThreshold
        self.edgeThreshold = edgeThreshold
        self.sigma = sigma
        self._sift = None

    def _ensure_sift(self):
        if self._sift is None:
            if not hasattr(cv2, "SIFT_create"):
                raise RuntimeError(
                    "SIFT not available in your OpenCV build. Install `opencv-contrib-python`."
                )
            self._sift = cv2.SIFT_create(
                nfeatures=self.n_features,
                contrastThreshold=self.contrastThreshold,
                edgeThreshold=self.edgeThreshold,
                sigma=self.sigma
            )

    def fit(self, X, y=None):
        self._ensure_sift()
        return self

    def _img_to_gray(self, img):
        if img.ndim == 3 and img.shape[2] == 3:
            return cv2.cvtColor(img, cv2.COLOR_RGB2GRAY)
        return img

    def transform(self, X):
        self._ensure_sift()
        out = []
        for img in X:
            g = self._img_to_gray(img)
            kps, desc = self._sift.detectAndCompute(g, None)
            if desc is None or len(desc) == 0:
                mean = np.zeros(128, dtype=np.float32)
                std = np.zeros(128, dtype=np.float32)
                count = 0.0
            else:
                mean = desc.mean(axis=0)
                std = desc.std(axis=0)
                count = float(len(desc))
            vec = np.concatenate([mean, std, np.array([count], dtype=np.float32)], axis=0)
            out.append(vec.astype(np.float32))
        return np.vstack(out)

    def detect_keypoints(self, img_single):
        """Return keypoints for visualization purposes."""
        self._ensure_sift()
        g = self._img_to_gray(img_single)
        kps = self._sift.detect(g, None)
        return kps


# HOG+SIFT
class HOGSIFTConcatTransformer(BaseEstimator, TransformerMixin):
    """
    Computes HOG and SIFT features, then concatenates them:
      X -> [HOG(X) | SIFT(X)]
    Optional per-branch weights let you emphasize one feature family.
    """

    def __init__(
            self,
            hog_params=None,
            sift_params=None,
            hog_weight=1.0,
            sift_weight=1.0,
    ):
        self.hog_params = hog_params or {}
        self.sift_params = sift_params or {}
        self.hog_weight = float(hog_weight)
        self.sift_weight = float(sift_weight)
        self._hog = HOGTransformer(**self.hog_params)
        self._sift = SIFTTransformer(**self.sift_params)

    def fit(self, X, y=None):
        self._hog.fit(X, y)
        self._sift.fit(X, y)
        return self

    def transform(self, X):
        H = self._hog.transform(X).astype(np.float32, copy=False)
        S = self._sift.transform(X).astype(np.float32, copy=False)
        if self.hog_weight != 1.0:
            H = H * self.hog_weight
        if self.sift_weight != 1.0:
            S = S * self.sift_weight
        return np.hstack([H, S]).astype(np.float32, copy=False)


def make_pipeline(
        feat_type="hog",
        hog_params=None,
        sift_params=None,
        pca_n=None,
        C=1.0,
        hog_weight=1.0,
        sift_weight=1.0,
):
    if feat_type == "hog":
        feat = HOGTransformer(**(hog_params or {}))
    elif feat_type == "sift":
        feat = SIFTTransformer(**(sift_params or {}))
    elif feat_type in ("hog+sift", "concat", "hog_sift"):
        feat = HOGSIFTConcatTransformer(
            hog_params=(hog_params or {}),
            sift_params=(sift_params or {}),
            hog_weight=hog_weight,
            sift_weight=sift_weight,
        )
    else:
        raise ValueError("feat_type must be 'hog', 'sift', or 'hog+sift'")

    steps = [("feat", feat), ("scaler", StandardScaler(with_mean=True))]
    if pca_n is not None:
        steps.append(("pca", PCA(n_components=pca_n, svd_solver="auto", random_state=RANDOM_STATE)))
    steps.append(("svm", LinearSVC(C=C, dual=False, max_iter=10000, random_state=RANDOM_STATE)))
    return Pipeline(steps)


def _feature_dim_of_transformer(transformer, example_img):
    """Probe feature dimensionality with one image."""
    f = transformer.transform(np.expand_dims(example_img, 0))
    return f.shape[1]


def _build_feats_memmap(n_rows, n_cols, dtype=np.float32):
    tmp_dir = Path("feature_cache")
    tmp_dir.mkdir(exist_ok=True)
    path = tmp_dir / f"feats_{n_rows}x{n_cols}_{int(time.time())}.dat"
    arr = np.memmap(path, mode="w+", dtype=dtype, shape=(n_rows, n_cols))
    return arr, path


def _extract_features_batched(paths, indices, transformer, probe_img, batch_size=BATCH_SIZE, pbar_desc=None,
                              pbar_position=2, pbar_leave=False):
    fdim = _feature_dim_of_transformer(transformer, probe_img)
    feats, path = _build_feats_memmap(len(indices), fdim, dtype=np.float32)
    write_ptr = 0
    desc = pbar_desc or f"Extract {type(transformer).__name__} (n={len(indices)})"
    with tqdm(total=len(indices), desc=desc, unit="img", position=pbar_position, leave=pbar_leave,
              dynamic_ncols=True) as pbar:
        for Xb, idxs in batch_iterator(paths, indices, batch_size):
            Fb = transformer.transform(Xb).astype(np.float32, copy=False)
            n = len(idxs)
            feats[write_ptr:write_ptr + n] = Fb
            write_ptr += n
            pbar.update(n)
    feats.flush()
    return feats, path


def fit_eval_pipeline(paths, y, params, cv_splits=5, random_state=RANDOM_STATE):
    """
    Train/validate one param set using stratified K-fold; returns mean accuracy and per-fold scores.
    Featurization happens in batches directly from disk paths.
    """
    feat_type = params["feat__type"]

    if feat_type == "hog":
        feat_params = dict(
            orientations=params["hog__orientations"],
            pixels_per_cell=params["hog__pixels_per_cell"],
            cells_per_block=params["hog__cells_per_block"],
            block_norm=params.get("hog__block_norm", "L2-Hys"),
        )
        transformer = HOGTransformer(**feat_params)

    elif feat_type == "sift":
        feat_params = dict(
            n_features=params.get("sift__n_features", 0),
            contrastThreshold=params.get("sift__contrastThreshold", 0.04),
            edgeThreshold=params.get("sift__edgeThreshold", 10),
            sigma=params.get("sift__sigma", 1.6),
        )
        transformer = SIFTTransformer(**feat_params)

    elif feat_type in ("hog+sift", "concat", "hog_sift"):
        hogp = dict(
            orientations=params["hog__orientations"],
            pixels_per_cell=params["hog__pixels_per_cell"],
            cells_per_block=params["hog__cells_per_block"],
            block_norm=params.get("hog__block_norm", "L2-Hys"),
        )
        siftp = dict(
            n_features=params.get("sift__n_features", 0),
            contrastThreshold=params.get("sift__contrastThreshold", 0.04),
            edgeThreshold=params.get("sift__edgeThreshold", 10),
            sigma=params.get("sift__sigma", 1.6),
        )
        transformer = HOGSIFTConcatTransformer(
            hog_params=hogp,
            sift_params=siftp,
            hog_weight=params.get("concat__hog_weight", 1.0),
            sift_weight=params.get("concat__sift_weight", 1.0),
        )

    else:
        raise ValueError("Unknown feat__type")

    pca_n = params.get("pca__n_components", None)
    C = params["svm__C"]

    probe_img = load_and_preprocess_image(paths[0])

    skf = StratifiedKFold(n_splits=cv_splits, shuffle=True, random_state=random_state)
    fold_scores = []

    with tqdm(total=cv_splits, desc="CV folds", position=1, leave=False, dynamic_ncols=True) as foldbar:
        for fold_i, (train_idx, val_idx) in enumerate(skf.split(np.zeros(len(y)), y), start=1):
            transformer.fit(None)

            Xtr_feats, tr_path = _extract_features_batched(
                paths, train_idx, transformer, probe_img,
                pbar_desc=f"Extract {type(transformer).__name__} [train f{fold_i}]", pbar_position=2,
                pbar_leave=False
            )
            Xval_feats, val_path = _extract_features_batched(
                paths, val_idx, transformer, probe_img,
                pbar_desc=f"Extract {type(transformer).__name__} [val   f{fold_i}]",
                pbar_position=3,
                pbar_leave=False
            )

            Xtr = np.asarray(Xtr_feats)
            Xval = np.asarray(Xval_feats)

            n_tr, d_tr = Xtr.shape
            dual = d_tr > n_tr

            steps = [("scaler", StandardScaler(with_mean=True))]
            use_pca_n = None
            if pca_n is not None:
                max_pca = min(n_tr, d_tr) - 1
                if max_pca >= 1 and pca_n <= max_pca:
                    use_pca_n = pca_n
                else:
                    tqdm.write(f"  -> Skipping PCA (n_components={pca_n} > max={max_pca})")
            if use_pca_n is not None:
                steps.append(("pca", PCA(n_components=use_pca_n, svd_solver="auto", random_state=random_state)))
            steps.append(("svm", LinearSVC(C=C, dual=dual, max_iter=10000, random_state=random_state)))
            clf = Pipeline(steps)

            clf.fit(Xtr, y[train_idx])
            preds = clf.predict(Xval)
            acc = accuracy_score(y[val_idx], preds)
            fold_scores.append(acc)

            try:
                Xtr_feats.flush();
                del Xtr_feats
                Xval_feats.flush();
                del Xval_feats
                del Xtr, Xval
                gc.collect()
                os.remove(tr_path)
                os.remove(val_path)
            except Exception:
                pass

            foldbar.update(1)

    return float(np.mean(fold_scores)), fold_scores


def save_state(state_path, state):
    tmp = state_path.with_suffix(".tmp")
    dump(state, tmp)
    os.replace(tmp, state_path)


def load_state(state_path):
    return load(state_path)


def run_tuning(
        paths, y,
        param_grid,
        checkpoint_path=CHECKPOINT_PATH,
        best_model_path=BEST_MODEL_PATH,
        cv_splits=5,
        save_every=1,
        resume=True,
        refit_best_on_full=True
):
    checkpoint_path.parent.mkdir(parents=True, exist_ok=True)
    best_model_path.parent.mkdir(parents=True, exist_ok=True)

    param_list = list(ParameterGrid(param_grid))
    print(f"\n[INFO] Generated {len(param_list)} parameter combinations to evaluate")

    if resume and checkpoint_path.exists():
        state = load_state(checkpoint_path)
        print(f"[Resume] Loaded state with {state['next_idx']} / {len(param_list)} evaluated.")
    else:
        state = dict(
            param_list=param_list,
            results=[],
            best_score=-np.inf,
            best_params=None,
            next_idx=0,
            cv_splits=cv_splits,
            started_at=time.time(),
        )
        print(f"[INFO] Starting fresh tuning run")

    last_save = 0
    total = len(param_list)

    print(f"[INFO] Will evaluate from index {state['next_idx']} to {total}")

    with tqdm(total=total, initial=state["next_idx"], desc="Tuning grid", position=0, leave=True,
              dynamic_ncols=True) as tbar:
        while state["next_idx"] < len(state["param_list"]):
            idx = state["next_idx"]
            params = state["param_list"][idx]
            t0 = time.time()
            tqdm.write(f"\n[{idx + 1}/{len(param_list)}] Evaluating: {params}")

            try:
                mean_acc, fold_scores = fit_eval_pipeline(paths, y, params, cv_splits=cv_splits)
                dt = time.time() - t0

                state["results"].append({
                    "idx": idx,
                    "params": params,
                    "mean_accuracy": mean_acc,
                    "fold_scores": fold_scores,
                    "seconds": dt,
                })

                tqdm.write(f"  -> Completed in {dt:.1f}s, mean accuracy: {mean_acc:.4f}")
            except Exception as e:
                tqdm.write(f"  -> ERROR: {str(e)}")
                import traceback
                tqdm.write(traceback.format_exc())
                state["results"].append({
                    "idx": idx,
                    "params": params,
                    "error": str(e),
                    "seconds": time.time() - t0,
                })
                state["next_idx"] += 1
                last_save += 1
                tbar.update(1)
                if last_save >= save_every:
                    save_state(checkpoint_path, state)
                    tqdm.write(f"  [Checkpoint saved after error]: {checkpoint_path}")
                    last_save = 0
                continue

            state["next_idx"] += 1
            last_save += 1
            tbar.update(1)

            if mean_acc > state["best_score"]:
                state["best_score"] = mean_acc
                state["best_params"] = params
                tqdm.write(f"  -> New best: {mean_acc:.4f}")

                if refit_best_on_full:
                    tqdm.write("  -> Refit best on full data (batched features)...")
                    feat_type = params["feat__type"]

                    if feat_type == "hog":
                        feat_params = dict(
                            orientations=params["hog__orientations"],
                            pixels_per_cell=params["hog__pixels_per_cell"],
                            cells_per_block=params["hog__cells_per_block"],
                            block_norm=params.get("hog__block_norm", "L2-Hys"),
                        )
                        transformer = HOGTransformer(**feat_params)
                    elif feat_type == "sift":
                        feat_params = dict(
                            n_features=params.get("sift__n_features", 0),
                            contrastThreshold=params.get("sift__contrastThreshold", 0.04),
                            edgeThreshold=params.get("sift__edgeThreshold", 10),
                            sigma=params.get("sift__sigma", 1.6),
                        )
                        transformer = SIFTTransformer(**feat_params)
                    elif feat_type in ("hog+sift", "concat", "hog_sift"):
                        hogp = dict(
                            orientations=params["hog__orientations"],
                            pixels_per_cell=params["hog__pixels_per_cell"],
                            cells_per_block=params["hog__cells_per_block"],
                            block_norm=params.get("hog__block_norm", "L2-Hys"),
                        )
                        siftp = dict(
                            n_features=params.get("sift__n_features", 0),
                            contrastThreshold=params.get("sift__contrastThreshold", 0.04),
                            edgeThreshold=params.get("sift__edgeThreshold", 10),
                            sigma=params.get("sift__sigma", 1.6),
                        )
                        feat_params = {
                            "hog_params": hogp,
                            "sift_params": siftp,
                            "hog_weight": params.get("concat__hog_weight", 1.0),
                            "sift_weight": params.get("concat__sift_weight", 1.0),
                        }
                        transformer = HOGSIFTConcatTransformer(**feat_params)
                    else:
                        raise ValueError(f"Unknown feat_type: {feat_type}")

                    probe_img = load_and_preprocess_image(paths[0])
                    transformer.fit(None)
                    all_indices = np.arange(len(paths))
                    X_feats, feats_path = _extract_features_batched(
                        paths, all_indices, transformer, probe_img,
                        pbar_desc="Extract features [full dataset]",
                        pbar_position=1, pbar_leave=False
                    )

                    X_all = np.asarray(X_feats)
                    n_all, d_all = X_all.shape
                    dual = d_all > n_all

                    steps = [("scaler", StandardScaler(with_mean=True))]
                    pca_n = params.get("pca__n_components", None)
                    use_pca_n = None
                    if pca_n is not None:
                        max_pca = min(n_all, d_all) - 1
                        if max_pca >= 1 and pca_n <= max_pca:
                            use_pca_n = pca_n
                        else:
                            tqdm.write(f"  -> Skipping PCA (n_components={pca_n} > max={max_pca})")
                    if use_pca_n is not None:
                        steps.append(("pca", PCA(n_components=use_pca_n, svd_solver="auto", random_state=RANDOM_STATE)))
                    steps.append(
                        ("svm", LinearSVC(C=params["svm__C"], dual=dual, max_iter=10000, random_state=RANDOM_STATE)))
                    best_pipe = Pipeline(steps)
                    best_pipe.fit(X_all, y)

                    dump({
                        "feature_type": feat_type,
                        "feature_params": feat_params,
                        "post_feat_pipeline": best_pipe
                    }, best_model_path)

                    tqdm.write(f"  -> Saved best model to: {best_model_path}")

                    try:
                        X_feats.flush();
                        del X_feats
                        del X_all
                        gc.collect()
                        os.remove(feats_path)
                    except Exception:
                        pass

            if last_save >= save_every:
                save_state(checkpoint_path, state)
                tqdm.write(f"  [Checkpoint saved]: {checkpoint_path}")
                last_save = 0

    save_state(checkpoint_path, state)
    print("\n==== Tuning complete ====")
    print(f"Best CV acc: {state['best_score']:.4f}")
    print(f"Best params: {state['best_params']}")
    print(f"State saved at: {checkpoint_path}")
    if refit_best_on_full and best_model_path.exists():
        print(f"Best model at: {best_model_path}")
    return state



In [4]:
def make_feature_examples_pdfs(paths, label_map, base_pdf_path=PDF_PATH, hog_params=None, sift_params=None):
    base = Path(base_pdf_path)
    classes = sorted({p.parent.name for p in paths})

    first_idx_by_class = {}
    for i, p in enumerate(paths):
        cls = p.parent.name
        if cls not in first_idx_by_class:
            first_idx_by_class[cls] = i
        if len(first_idx_by_class) == len(classes):
            break

    hog_t = HOGTransformer(**(hog_params or {}))
    sift_t = SIFTTransformer(**(sift_params or {}))

    for cls in classes:
        idx = first_idx_by_class.get(cls)
        if idx is None:
            print(f"[Warning] No example found for class: {cls}")
            continue

        img = load_and_preprocess_image(paths[idx])
        _, hog_img = hog_t.transform_with_viz(img)
        kps = sift_t.detect_keypoints(img)
        img_kp_rgb = cv2.cvtColor(
            cv2.drawKeypoints(cv2.cvtColor(img, cv2.COLOR_RGB2BGR), kps, None,
                              flags=cv2.DRAW_MATCHES_FLAGS_DRAW_RICH_KEYPOINTS),
            cv2.COLOR_BGR2RGB
        )

        cls_pdf = base.with_name(f"{base.stem}_{cls}{base.suffix or '.pdf'}")
        with PdfPages(cls_pdf) as pdf:
            fig = plt.figure(figsize=(12, 4), constrained_layout=True)
            fig.suptitle(f"Class: {cls}", fontsize=14)
            for i_ax, (title, im) in enumerate([("Padded original", img),
                                                ("HOG visualization", hog_img),
                                                (f"SIFT keypoints (n={len(kps)})", img_kp_rgb)], 1):
                ax = fig.add_subplot(1, 3, i_ax)
                ax.imshow(im)
                ax.set_title(title)
                ax.axis("off")
            pdf.savefig(fig)
            plt.close(fig)
        print(f"[PDF] Saved {cls_pdf}")



In [5]:
# Main execution for full search
if __name__ == "__main__":
    # 1) Load all paths and labels
    print(f"[INFO] Looking for data in: {DATA_DIR}")
    if not DATA_DIR.exists():
        print(f"[ERROR] Data directory does not exist: {DATA_DIR}")
        print(f"[ERROR] Please check the path. Current working directory: {Path.cwd()}")
        exit(1)

    all_paths, all_y, label_map = enumerate_paths_and_labels(DATA_DIR)
    print(f"Found {len(all_paths)} images, classes: {label_map}")

    if len(all_paths) == 0:
        print("[ERROR] No images found! Check your DATA_DIR and IMG_EXTS settings.")
        exit(1)

    # 2) Create stratified subset for grid search
    paths, y, subset_indices = create_stratified_subset(
        all_paths, all_y,
        subset_size=SUBSET_SIZE,
        min_per_class=MIN_SAMPLES_PER_CLASS
    )

    # Ensure each class has at least cv_splits samples for StratifiedKFold
    cv_splits = 2
    counts = np.bincount(y)
    if (counts < cv_splits).any():
        print(
            f"[ERROR] Every class needs at least {cv_splits} samples for StratifiedKFold; got counts={counts.tolist()}")
        print(f"[ERROR] Try increasing SUBSET_SIZE or decreasing cv_splits")
        exit(1)

    # 3) Define search space (both HOG and SIFT)
    param_grid = [
        # HOG branch
        {
            "feat__type": ["hog"],
            "hog__orientations": [6, 9, 12],
            "hog__pixels_per_cell": [(8, 8), (8, 16), (16, 16)],
            "hog__cells_per_block": [(2, 2), (3, 3)],
            "hog__block_norm": ["L2-Hys"],
            "pca__n_components": [128, 256],
            "svm__C": [0.002, 0.25, 1.0, 4.0],
        },
        # SIFT branch
        {
            "feat__type": ["sift"],
            "sift__n_features": [0, 600, 1000],
            "sift__contrastThreshold": [0.02, 0.04, 0.08],
            "sift__edgeThreshold": [5, 10, 15],
            "sift__sigma": [1.2, 1.6, 1.8],
            "pca__n_components": [128, 256],
            "svm__C": [0.002, 0.25, 1.0, 4.0],
        },
        # # HOG+SIFT branch (uncomment if needed)
        # {
        #     "feat__type": ["hog+sift"],
        #     "hog__orientations": [9],
        #     "hog__pixels_per_cell": [(8, 8)],
        #     "hog__cells_per_block": [(2, 2)],
        #     "hog__block_norm": ["L2-Hys"],
        #     "sift__n_features": [0, 600],
        #     "sift__contrastThreshold": [0.04],
        #     "sift__edgeThreshold": [10],
        #     "sift__sigma": [1.6],
        #     "concat__hog_weight": [1.0, 2.0],
        #     "concat__sift_weight": [1.0, 2.0],
        #     "pca__n_components": [128, 256],
        #     "svm__C": [0.002, 0.25, 1.0, 4.0],
        # },
    ]

    # 4) Run (or resume) tuning on subset
    state = run_tuning(
        paths, y,
        param_grid=param_grid,
        checkpoint_path=CHECKPOINT_PATH,
        best_model_path=BEST_MODEL_PATH,
        cv_splits=cv_splits,
        save_every=1,
        resume=True,
        refit_best_on_full=False  # Set to True if you want to refit on full data after finding best params
    )

    # 5) Optional: After grid search, you can retrain the best model on the full dataset
    print("\n" + "=" * 60)
    print("GRID SEARCH COMPLETED ON SUBSET")
    print("=" * 60)
    print(f"To train on the full dataset with best params, use:")
    print(f"  paths_full = all_paths")
    print(f"  y_full = all_y")
    print(f"  best_params = {state['best_params']}")

[INFO] Looking for data in: ../data/OCT2017 /train
Found 83484 images, classes: {'CNV': 0, 'DME': 1, 'DRUSEN': 2, 'NORMAL': 3}

[SUBSET] Created stratified subset:
  Original size: 83484
  Subset size: 16696 (20.0%)
  Samples per class:
    Class 0: 7441 / 37205 (20.0%)
    Class 1: 2269 / 11348 (20.0%)
    Class 2: 1723 / 8616 (20.0%)
    Class 3: 5263 / 26315 (20.0%)

[INFO] Generated 792 parameter combinations to evaluate
[Resume] Loaded state with 229 / 792 evaluated.
[INFO] Will evaluate from index 229 to 792


Tuning grid:  29%|██▉       | 229/792 [00:00<?, ?it/s]


[230/792] Evaluating: {'feat__type': 'sift', 'pca__n_components': 128, 'sift__contrastThreshold': 0.02, 'sift__edgeThreshold': 15, 'sift__n_features': 600, 'sift__sigma': 1.2, 'svm__C': 0.25}



CV folds:   0%|          | 0/2 [00:00<?, ?it/s]

Extract SIFTTransformer [train f1]:   0%|          | 0/8348 [00:00<?, ?img/s]

Extract SIFTTransformer [train f1]:   1%|          | 64/8348 [00:00<00:59, 139.60img/s]

Extract SIFTTransformer [train f1]:   2%|▏         | 128/8348 [00:00<00:55, 148.98img/s]

Extract SIFTTransformer [train f1]:   2%|▏         | 192/8348 [00:01<00:55, 146.51img/s]

Extract SIFTTransformer [train f1]:   3%|▎         | 256/8348 [00:01<00:56, 143.08img/s]

Extract SIFTTransformer [train f1]:   4%|▍         | 320/8348 [00:02<00:56, 143.31img/s]

Extract SIFTTransformer [train f1]:   5%|▍         | 384/8348 [00:02<00:56, 140.29img/s]

Extract SIFTTransformer [train f1]:   5%|▌         | 448/8348 [00:03<00:56, 140.59img/s]

Extract SIFTTransformer [train f1]:   6%|▌         | 512/8348 [00:03<00:56, 138.92img/s]

Extract SIFTTransformer [train f1]:   7%|▋         | 576/8348 [00:04<00:55, 138.86img/s]

Extract SIFTTransformer [train f1]:   8%|▊         | 640/8348 

  -> Completed in 211.4s, mean accuracy: 0.7595
  [Checkpoint saved]: checkpoints/tuning_state.pkl

[231/792] Evaluating: {'feat__type': 'sift', 'pca__n_components': 128, 'sift__contrastThreshold': 0.02, 'sift__edgeThreshold': 15, 'sift__n_features': 600, 'sift__sigma': 1.2, 'svm__C': 1.0}


...

  -> Completed in 197.1s, mean accuracy: 0.7431
  [Checkpoint saved]: checkpoints/tuning_state.pkl

[301/792] Evaluating: {'feat__type': 'sift', 'pca__n_components': 128, 'sift__contrastThreshold': 0.04, 'sift__edgeThreshold': 10, 'sift__n_features': 600, 'sift__sigma': 1.2, 'svm__C': 0.002}



CV folds:   0%|          | 0/2 [00:00<?, ?it/s]

Extract SIFTTransformer [train f1]:   0%|          | 0/8348 [00:00<?, ?img/s]

Extract SIFTTransformer [train f1]:   1%|          | 64/8348 [00:00<00:43, 189.71img/s]

Extract SIFTTransformer [train f1]:   2%|▏         | 128/8348 [00:00<00:41, 196.49img/s]

Extract SIFTTransformer [train f1]:   2%|▏         | 192/8348 [00:00<00:42, 193.08img/s]

Extract SIFTTransformer [train f1]:   3%|▎         | 256/8348 [00:01<00:42, 190.04img/s]

Extract SIFTTransformer [train f1]:   4%|▍         | 320/8348 [00:01<00:42, 190.03img/s]

Extract SIFTTransformer [train f1]:   5%|▍         | 384/8348 [00:02<00:42, 188.34img/s]

Extract SIFTTransformer [train f1]:   5%|▌         | 448/8348 [00:02<00:41, 189.96img/s]

Extract SIFTTransformer [train f1]:   6%|▌         | 512/8348 [00:02<00:41, 188.09img/s]

Extract SIFTTransformer [train f1]:   7%|▋         | 576/8348 [00:03<00:41, 186.94img/s]

Extract SIFTTransformer [train f1]:   8%|▊         | 640/8348 

  -> Completed in 229.2s, mean accuracy: 0.7117
  [Checkpoint saved]: checkpoints/tuning_state.pkl

[302/792] Evaluating: {'feat__type': 'sift', 'pca__n_components': 128, 'sift__contrastThreshold': 0.04, 'sift__edgeThreshold': 10, 'sift__n_features': 600, 'sift__sigma': 1.2, 'svm__C': 0.25}



CV folds:   0%|          | 0/2 [00:00<?, ?it/s]

Extract SIFTTransformer [train f1]:   0%|          | 0/8348 [00:00<?, ?img/s]

Extract SIFTTransformer [train f1]:   1%|          | 64/8348 [00:00<00:56, 145.44img/s]

Extract SIFTTransformer [train f1]:   2%|▏         | 128/8348 [00:00<00:51, 160.36img/s]

Extract SIFTTransformer [train f1]:   2%|▏         | 192/8348 [00:01<00:49, 163.64img/s]

Extract SIFTTransformer [train f1]:   3%|▎         | 256/8348 [00:01<00:48, 167.00img/s]

Extract SIFTTransformer [train f1]:   4%|▍         | 320/8348 [00:01<00:46, 171.42img/s]

Extract SIFTTransformer [train f1]:   5%|▍         | 384/8348 [00:02<00:45, 173.33img/s]

Extract SIFTTransformer [train f1]:   5%|▌         | 448/8348 [00:02<00:44, 176.74img/s]

Extract SIFTTransformer [train f1]:   6%|▌         | 512/8348 [00:03<00:45, 173.31img/s]

Extract SIFTTransformer [train f1]:   7%|▋         | 576/8348 [00:03<00:45, 171.11img/s]

Extract SIFTTransformer [train f1]:   8%|▊         | 640/8348 

KeyboardInterrupt: 